In [21]:
path_intermed='/home/www/pschmitt/provide/aggregate_data/github/provide/countries/resolution_1_deg/aggregated_data_intermediate/'
path='/home/www/pschmitt/provide/aggregate_data/github/provide/countries/resolution_1_deg/aggregated_data/'

In [22]:
import xarray as xr
import numpy as np

In [166]:
gcms_mesmer = [# 'ACCESS-CM2',  precipitation data not everywhere available ,
               # 'MCM-UA-1-0', no precipitation data
               'ACCESS-ESM1-5', 'CESM2-WACCM', 'CESM2', 'CMCC-CM2-SR5', 'CNRM-CM6-1-HR',
               'CNRM-CM6-1', 'CNRM-ESM2-1', 'CanESM5', 'E3SM-1-1', 'FGOALS-f3-L',
               'FGOALS-g3', 'HadGEM3-GC31-LL', 'HadGEM3-GC31-MM', 'IPSL-CM6A-LR', 'MPI-ESM1-2-HR',
               'MPI-ESM1-2-LR' , 'MRI-ESM2-0', 'NorESM2-LM', 'NorESM2-MM', 'UKESM1-0-LL']
quantiles_mesmer = ['0.05', '0.25', '0.5', '0.75', '0.95']
scenarios_mesmer = ['CurPol', 'GS', 'LD','ModAct','Ref','Ren','Neg', 'SP','ssp119','ssp534-over']
countries_l = list(dict_countries.keys())

In [167]:
len(countries_l)

50

In [168]:
countries_l = []
for c in dict_countries.keys():
    if len(dict_countries[c])>0:
        countries_l.append(c)

In [211]:
for c in countries_l:
    try:
        for scen in scenarios_mesmer:
            for gcm in gcms_mesmer: 
                ds_intermed_total = xr.open_dataset(path_intermed + f'{c}/total_data/{c}_{scen}_{gcm}_0.5_total_data.nc').volume.sel(time=2100)
                ds_intermed_map_sum = xr.open_dataset(path_intermed + f'{c}/map_data/{c}_{scen}_{gcm}_0.5_map_data.nc').volume.sel(time=2100).sum(dim='lat').sum(dim='lon')
                np.testing.assert_allclose(ds_intermed_map_sum,ds_intermed_total)
    except FileNotFoundError:
        print(c)

ARM
ATA
ATF
AZE
HMD
IDN
KEN
TZA
UGA
ZAF


In [212]:
zero_land_l = []
for c in countries_l:
    try:
        for scen in scenarios_mesmer:
            ds_total = xr.open_dataset(path + f'{c}/{c}_{scen}_timeseries.nc').volume.sel(time=2100).sel(quantile=0.5)
            ds_map_sum = xr.open_dataset(path + f'{c}/{c}_{scen}_map.nc').volume.sel(time=2100).sel(quantile=0.5).sum(dim='lat', skipna=True).sum(dim='lon', skipna=True)       
            if np.isnan(ds_total) and ds_map_sum==0:
                zero_land_l.append(f'{c}_{scen}')
            else:
                np.testing.assert_allclose(ds_map_sum,ds_total, rtol= 0.02)
                np.testing.assert_allclose(ds_map_sum,ds_total, atol= 1)

    except:
        try:
            for scen in scenarios_mesmer:
                ds_total = xr.open_dataset(path + f'{c}/{c}_{scen}_timeseries.nc').volume.sel(time=2100).sel(quantile=0.5)
                ds_map_sum = xr.open_dataset(path + f'{c}/{c}_{scen}_map.nc').volume.sel(time=2100).sum(dim='lat').sum(dim='lon').sel(quantile=0.5)
                if np.abs(ds_map_sum-ds_total).max()>1.5:
                    print(f'absolute difference: {np.abs(ds_map_sum-ds_total).max().values.round(1)} for {c},{scen}')
                np.testing.assert_allclose(ds_map_sum,ds_total, rtol= 0.1)
                np.testing.assert_allclose(ds_map_sum,ds_total, atol= 3)

            print(f'{c} needed rtol=0.1')
        except FileNotFoundError:
            print(c)

AFG needed rtol=0.1
ARM
ATA
ATF
AUT needed rtol=0.1
AZE
absolute difference: 1.6 for BOL,Ref
BOL needed rtol=0.1
absolute difference: 2.3 for CHN,Neg
CHN needed rtol=0.1
absolute difference: 2.0 for COL,LD
COL needed rtol=0.1
DEU needed rtol=0.1
FRA needed rtol=0.1
HMD
IDN
IRN needed rtol=0.1
ITA needed rtol=0.1
KAZ needed rtol=0.1
KEN
absolute difference: 1.9 for KGZ,ssp119
KGZ needed rtol=0.1
MNG needed rtol=0.1
NZL needed rtol=0.1
PER needed rtol=0.1
SWE needed rtol=0.1
TZA
UGA
UZB needed rtol=0.1
ZAF


**absolute difference is smaller than 2.3% for all scenarios, in four experiments (specific country-scenario differences in Bolivia, CHN, COL, KGZ) the uncertainties are larger than 1.5%** 

**Test with Patrick's quantile function**

In [213]:
def get_weighted_quantiles(ds, q_to_return=None,
                           return_weighted_total_quantiles=True):
    # Define the repetition scheme for each quantile
    quantile_repetitions = {
        0.05: 6,
        0.25: 9,
        0.50: 10,
        0.75: 9,
        0.95: 6
    }
    if q_to_return is None:
        q_to_return = list(quantile_repetitions.keys())
    
    duplicated_data_arrays = []
    
    # Iterate over each quantile, duplicating the data points as specified
    for quantile, repetitions in quantile_repetitions.items():
        quantile_data = ds.sel(quantile=quantile)
        for _ in range(repetitions):
            duplicated_data_arrays.append(quantile_data)
    
    combined_data = xr.concat(duplicated_data_arrays, dim='extra_quantiles')

    def add_attr(ds_return, ds):
        ds_return.attrs['grid_resolution'] = ds_structure.attrs['resolution']
        ds_result.attrs['grid_points_with_data'] = ds_structure.attrs['grid_points_with_data']

    if return_weighted_total_quantiles:
        # here we return the quantiles drawn from all realisations
        ds_return = combined_data.stack(
            sample=('gcm', 'extra_quantiles')).chunk({'sample': -1}).quantile(
            q_to_return, dim='sample')

    else:
        # here we return the quantiles for each gcm
        ds_return = combined_data.chunk({'extra_quantiles': -1}).quantile(
            q_to_return, dim='extra_quantiles')

    if 'grid_resolution' in ds.attrs:
        ds_return.attrs['grid_resolution'] = ds.attrs['grid_resolution']
        ds_return.attrs['grid_points_with_data'] = ds.attrs['grid_points_with_data']

    return ds_return


In [223]:
#for scen in scenarios_mesmer:
_qs_l = []
_qs_map_l = []

for q in quantiles_mesmer:
    _ds_intermed_total_l =[]
    _ds_intermed_map_l =[]

    for gcm in gcms_mesmer: 
        _ds_intermed_total = xr.open_dataset(path_intermed + f'CHN/total_data/CHN_{scen}_{gcm}_{q}_total_data.nc').volume.sel(time=2100)
        _ds_intermed_map = xr.open_dataset(path_intermed + f'CHN/map_data/CHN_{scen}_{gcm}_{q}_map_data.nc').volume.sel(time=2100) #.sum(dim='lat').sum(dim='lon')
        #np.testing.assert_allclose(ds_intermed_map_sum,ds_intermed_total)
        _ds_intermed_total_l.append(_ds_intermed_total)
        _ds_intermed_map_l.append(_ds_intermed_map)

    _qs_l.append(xr.concat(_ds_intermed_total_l, dim = 'gcm'))
    _qs_map_l.append(xr.concat(_ds_intermed_map_l, dim = 'gcm'))

_total = xr.concat(_qs_l, dim='quantile')
_map = xr.concat(_qs_map_l, dim='quantile')

ds_total_2020 = xr.open_dataset(path + f'CHN/CHN_{scen}_timeseries.nc').volume.sel(time=2020)
ds_total= xr.open_dataset(path + f'CHN/CHN_{scen}_timeseries.nc').volume.sel(time=2100)
np.testing.assert_allclose(get_weighted_quantiles(_total).values/(ds_total_2020.reference_2020_km3*1e9)*100, ds_total)

In [224]:
_map_total_quantiles = get_weighted_quantiles(_map.sum(dim='lon').sum(dim='lat'), q_to_return=0.5)/(ds_total_2020.reference_2020_km3*1e9)*100
_map_total_quantiles.values #.sum(dim='lon').sum(dim='lat').values

array([39.29880626])

In [226]:
_map_total_quantiles.values

array([39.29880626])

In [217]:
ds = _map.sum(dim='lon').sum(dim='lat')/(ds_total_2020.reference_2020_km3*1e9)*100

#ds = _map/(ds_total_2020.reference_2020_km3*1e9)*100

In [218]:
ds

<xarray.DataArray 'volume' (gcm: 20, scenario: 1, quantile: 5)>
array([[[50.9957216 , 39.32700413, 37.07808415, 36.85337187,
         23.16180655]],

       [[56.85192734, 55.39070707, 50.62811728, 44.15831257,
         31.4754163 ]],

       [[59.36599856, 41.88065921, 53.64313674, 40.06315943,
         34.33280219]],

       [[63.91809198, 37.85633308, 37.44071962, 46.17950596,
         31.82827834]],

       [[42.2865779 , 35.10642434, 39.79579952, 34.96882074,
         26.73328086]],

       [[51.35130462, 55.75599372, 44.36566462, 42.98749963,
         28.12223764]],

       [[57.44947192, 62.67687717, 38.34448371, 49.77602839,
         32.18109614]],
...
       [[48.30792512, 42.6520458 , 32.51080171, 27.33190732,
         18.78451048]],

       [[50.82562007, 38.3260486 , 39.41358516, 38.26790916,
         23.81974991]],

       [[45.72914242, 41.91272377, 39.2706084 , 25.80027595,
         18.52394023]],

       [[48.46261166, 48.36519252, 36.99470932, 31.52122994,
         21.8020242 ]],

       [[49.46923917, 47.76009616, 36.95937068, 35.58499767,
         19.1794325 ]],

       [[45.10786088, 39.15729461, 35.44870624, 33.07906629,
         19.18165067]],

       [[52.91389719, 45.59670027, 41.04688248, 37.3245603 ,
         24.48986584]]])
Coordinates:
    time            float64 2.1e+03
  * gcm             (gcm) object 'ACCESS-ESM1-5' 'CESM2-WACCM' ... 'UKESM1-0-LL'
  * scenario        (scenario) object 'CurPol'
  * quantile        (quantile) float64 0.05 0.25 0.5 0.75 0.95
    hydro_year      int64 2100
    hydro_month     int64 4
    calendar_year   int64 2100
    calendar_month  int64 1

In [219]:
q_to_return=0.5
return_weighted_total_quantiles = True
# Define the repetition scheme for each quantile
quantile_repetitions = {
    0.05: 6,
    0.25: 9,
    0.50: 10,
    0.75: 9,
    0.95: 6
}
if q_to_return is None:
    q_to_return = list(quantile_repetitions.keys())

duplicated_data_arrays = []

# Iterate over each quantile, duplicating the data points as specified
for quantile, repetitions in quantile_repetitions.items():
    quantile_data = ds.sel(quantile=quantile)
    for _ in range(repetitions):
        duplicated_data_arrays.append(quantile_data)

combined_data = xr.concat(duplicated_data_arrays, dim='extra_quantiles')

def add_attr(ds_return, ds):
    ds_return.attrs['grid_resolution'] = ds_structure.attrs['resolution']
    ds_result.attrs['grid_points_with_data'] = ds_structure.attrs['grid_points_with_data']

if return_weighted_total_quantiles:
    # here we return the quantiles drawn from all realisations
    ds_return = combined_data.stack(
        sample=('gcm', 'extra_quantiles')).chunk({'sample': -1}).quantile(
        q_to_return, dim='sample', interpolation='')

else:
    # here we return the quantiles for each gcm
    ds_return = combined_data.chunk({'extra_quantiles': -1}).quantile(
        q_to_return, dim='extra_quantiles',interpolation='midpoint')

if 'grid_resolution' in ds.attrs:
    ds_return.attrs['grid_resolution'] = ds.attrs['grid_resolution']
    ds_return.attrs['grid_points_with_data'] = ds.attrs['grid_points_with_data']
    
ds_return.sum().values

ValueError: '' is not a valid method. Use one of: dict_keys(['inverted_cdf', 'averaged_inverted_cdf', 'closest_observation', 'interpolated_inverted_cdf', 'hazen', 'weibull', 'linear', 'median_unbiased', 'normal_unbiased', 'lower', 'higher', 'midpoint', 'nearest'])

In [ ]:
ds_return.values

In [ ]:
_map_total_quantiles = get_weighted_quantiles(_map, q_to_return=0.5)/(ds_total_2020.reference_2020_km3*1e9)*100
_map_total_quantiles.sum(dim='lon').sum(dim='lat').values

In [ ]:
_map_total_quantiles = get_weighted_quantiles(_map.sum(dim='lon').sum(dim='lat'), return_weighted_total_quantiles=True)/(ds_total_2020.reference_2020_km3*1e9)*100
_map_total_quantiles.values #.sum(dim='lon').sum(dim='lat').values

In [ ]:
_map_total_quantiles = get_weighted_quantiles(_map, return_weighted_total_quantiles=False)/(ds_total_2020.reference_2020_km3*1e9)*100
_map_total_quantiles.sum(dim='lon').sum(dim='lat').values

array([[21.8020242 ],
       [32.13746158],
       [39.29880626],
       [45.72914242],
       [55.75599372]])

In [87]:
ds_total

<xarray.DataArray 'volume' (quantile: 5, scenario: 1)>
array([[21.802024],
       [32.137462],
       [39.298806],
       [45.729142],
       [55.755994]])
Coordinates:
    time            float64 2.1e+03
  * scenario        (scenario) object 'CurPol'
    hydro_year      int64 ...
    hydro_month     int64 ...
    calendar_year   int64 ...
    calendar_month  int64 ...
  * quantile        (quantile) float64 0.05 0.25 0.5 0.75 0.95
Attributes:
    unit:                in % relative to total value of 2020 (see reference_...
    reference_2020_km3:  2803.0721360024922

In [61]:
_m 

<xarray.DataArray 'volume' (gcm: 20, scenario: 1, quantile: 5)>
array([[[1.42944686e+12, 1.10236429e+12, 1.03932545e+12, 1.03302660e+12,
         6.49242145e+11]],

       [[1.59360053e+12, 1.55264148e+12, 1.41914265e+12, 1.23778936e+12,
         8.82278624e+11]],

       [[1.66407176e+12, 1.17394509e+12, 1.50365582e+12, 1.12299926e+12,
         9.62373212e+11]],

       [[1.79167023e+12, 1.06114032e+12, 1.04949038e+12, 1.29444486e+12,
         8.92169602e+11]],

       [[1.18532328e+12, 9.84058398e+11, 1.11550497e+12, 9.80201271e+11,
         7.49353147e+11]],

       [[1.43941411e+12, 1.56288072e+12, 1.24360158e+12, 1.20497062e+12,
         7.88286607e+11]],

       [[1.61035014e+12, 1.75687808e+12, 1.07482354e+12, 1.39525798e+12,
         9.02059339e+11]],
...
       [[1.35410599e+12, 1.19556761e+12, 9.11301224e+11, 7.66133078e+11,
         5.26543379e+11]],

       [[1.42467879e+12, 1.07430679e+12, 1.10479122e+12, 1.07267710e+12,
         6.67684773e+11]],

       [[1.28182085e+12, 1.17484388e+12, 1.10078348e+12, 7.23200346e+11,
         5.19239407e+11]],

       [[1.35844196e+12, 1.35571124e+12, 1.03698839e+12, 8.83562813e+11,
         6.11126465e+11]],

       [[1.38665846e+12, 1.33874995e+12, 1.03599782e+12, 9.97473154e+11,
         5.37613328e+11]],

       [[1.26440588e+12, 1.09760721e+12, 9.93652807e+11, 9.27230090e+11,
         5.37675505e+11]],

       [[1.48321471e+12, 1.27810840e+12, 1.15057373e+12, 1.04623435e+12,
         6.86468605e+11]]])
Coordinates:
    time            float64 2.1e+03
  * gcm             (gcm) object 'ACCESS-ESM1-5' 'CESM2-WACCM' ... 'UKESM1-0-LL'
  * scenario        (scenario) object 'CurPol'
  * quantile        (quantile) float64 0.05 0.25 0.5 0.75 0.95
    hydro_year      int64 2100
    hydro_month     int64 4
    calendar_year   int64 2100
    calendar_month  int64 1
Attributes:
    unit:     m3

In [30]:
ds_intermed_map_sum

<xarray.DataArray 'volume' (gcm: 1, scenario: 1, quantile: 1)>
array([[[9.79728258e+11]]])
Coordinates:
    time            float64 2.1e+03
  * gcm             (gcm) object 'UKESM1-0-LL'
  * scenario        (scenario) object 'ssp534-over'
  * quantile        (quantile) float64 0.5
    hydro_year      int64 ...
    hydro_month     int64 ...
    calendar_year   int64 ...
    calendar_month  int64 ...

In [33]:
xr.open_dataset(path_intermed + f'CHN/total_data/CHN_{scen}_{gcm}_0.5_total_data.nc')

<xarray.Dataset>
Dimensions:         (time: 17, gcm: 1, scenario: 1, quantile: 1)
Coordinates:
  * time            (time) float64 2.02e+03 2.025e+03 ... 2.095e+03 2.1e+03
  * gcm             (gcm) object 'ACCESS-ESM1-5'
  * scenario        (scenario) object 'CurPol'
  * quantile        (quantile) float64 0.5
    hydro_year      (time) int64 ...
    hydro_month     (time) int64 ...
    calendar_year   (time) int64 ...
    calendar_month  (time) int64 ...
Data variables:
    volume          (gcm, scenario, quantile, time) float64 ...
    area            (gcm, scenario, quantile, time) float64 ...
    thinning_rate   (gcm, scenario, quantile, time) float64 ...

In [32]:
100*xr.open_dataset(path_intermed + f'CHN/total_data/CHN_{scen}_{gcm}_0.5_total_data.nc').volume.sel(time=2100)/xr.open_dataset(path_intermed + f'CHN/total_data/CHN_{scen}_{gcm}_0.5_total_data.nc').volume.sel(time=2020)

<xarray.DataArray 'volume' (gcm: 1, scenario: 1, quantile: 1)>
array([[[0.37078084]]])
Coordinates:
  * gcm             (gcm) object 'ACCESS-ESM1-5'
  * scenario        (scenario) object 'CurPol'
  * quantile        (quantile) float64 0.5
    hydro_month     int64 4
    calendar_month  int64 1

In [ ]:
for scen in scenarios_mesmer:
    ds_total = xr.open_dataset(path + f'CHN/CHN_{scen}_timeseries.nc').volume.sel(time=2020)
    ds_map_sum = xr.open_dataset(path + f'CHN/CHN_{scen}_map.nc').volume.sel(time=2020).sum(dim='lat').sum(dim='lon')
    np.testing.assert_allclose(ds_map_sum,ds_total)

**Ok, something happens between intermediate to the final data**, it works for year 2020, but not for other years

In [47]:
for scen in scenarios_mesmer:
    ds_total = xr.open_dataset(path + f'AUT/AUT_{scen}_timeseries.nc').volume.sel(time=2100)
    ds_map_sum = xr.open_dataset(path + f'AUT/AUT_{scen}_map.nc').volume.sel(time=2100).sum(dim='lat').sum(dim='lon')
    np.testing.assert_allclose(ds_map_sum,ds_total)


AssertionError: 
Not equal to tolerance rtol=1e-07, atol=0

Mismatched elements: 4 / 5 (80%)
Max absolute difference: 0.16669802
Max relative difference: 0.04211976
 x: array([[ 0.1123  ],
       [ 0.641496],
       [ 1.877965],...
 y: array([[ 0.1123  ],
       [ 0.638005],
       [ 1.89596 ],...

In [49]:
ds_total

<xarray.DataArray 'volume' (quantile: 5, scenario: 1)>
array([[ 0.1123  ],
       [ 0.638005],
       [ 1.89596 ],
       [ 3.957715],
       [12.671956]])
Coordinates:
    time            float64 2.1e+03
  * scenario        (scenario) object 'CurPol'
    hydro_year      int64 ...
    hydro_month     int64 ...
    calendar_year   int64 ...
    calendar_month  int64 ...
  * quantile        (quantile) float64 0.05 0.25 0.5 0.75 0.95
Attributes:
    unit:                in % relative to total value of 2020 (see reference_...
    reference_2020_km3:  13.099874484445312

In [53]:
ds_map_sum

<xarray.DataArray 'volume' (quantile: 5, scenario: 1)>
array([[ 0.11229955],
       [ 0.6414956 ],
       [ 1.87796497],
       [ 4.12441348],
       [12.52822662]])
Coordinates:
    time            float64 2.1e+03
  * scenario        (scenario) object 'CurPol'
    hydro_year      int64 2100
    hydro_month     int64 4
    calendar_year   int64 2100
    calendar_month  int64 1
  * quantile        (quantile) float64 0.05 0.25 0.5 0.75 0.95

In [52]:
ds_map_sum<=ds_total

<xarray.DataArray 'volume' (quantile: 5, scenario: 1)>
array([[ True],
       [False],
       [ True],
       [False],
       [ True]])
Coordinates:
    time            float64 2.1e+03
  * scenario        (scenario) object 'CurPol'
    hydro_year      int64 2100
    hydro_month     int64 4
    calendar_year   int64 2100
    calendar_month  int64 1
  * quantile        (quantile) float64 0.05 0.25 0.5 0.75 0.95

In [ ]:
ds_map_sum

In [44]:
for scen in scenarios_mesmer:
    ds_total = xr.open_dataset(path + f'CHN/CHN_{scen}_timeseries.nc').volume.sel(time=2100)
    ds_map_sum = xr.open_dataset(path + f'CHN/CHN_{scen}_map.nc').volume.sel(time=2100).sum(dim='lat').sum(dim='lon')
    try:
        np.testing.assert_allclose(ds_map_sum,ds_total)
    except:
        print(scen)

CurPol
GS
LD
ModAct
Ref
Ren
Neg
SP
ssp119
ssp534-over
